In [1]:
import os

from IPython.core.interactiveshell import InteractiveShell  #执行该代码可以使得当前nb支持多输出
InteractiveShell.ast_node_interactivity = "all" 
import numpy as np
import pandas as pd 
pd.options.display.max_rows = 8  

**作业**
综合运用stack/unstack，pivot/melt

In [2]:
#有可能是版本问题，需要加入.strftime('%Y-%m-%d')
data = pd.read_csv('../examples/macrodata.csv')
data.index = pd.PeriodIndex(year=data.year, quarter=data.quarter,name='date').to_timestamp('D', 'end').strftime('%Y-%m-%d')
data = data.reindex(columns=pd.Index(['realgdp', 'infl', 'unemp'], name='item'))
print(data)


item          realgdp  infl  unemp
date                              
1959-03-31   2710.349  0.00    5.8
1959-06-30   2778.801  2.34    5.1
1959-09-30   2775.488  2.74    5.3
1959-12-31   2785.204  0.27    5.6
...               ...   ...    ...
2008-12-31  13141.920 -8.79    6.9
2009-03-31  12925.410  0.94    8.1
2009-06-30  12901.504  3.37    9.2
2009-09-30  12990.341  3.56    9.6

[203 rows x 3 columns]


**作业1:**
data通过stack/melt获得ldata

In [3]:
#请输入data使用stack实现的代码（不得使用melt）
data = data.reset_index()

ldata= data.set_index('date').stack().reset_index()
ldata.columns = ['date', 'item', 'value']
ldata.head()

# 请输出data使用melt实现的代码（不得使用stack）
#data = data.reset_index()
#ldata = pd.melt(data, id_vars=['date'], value_vars=['realgdp', 'infl', 'unemp'], var_name='item', value_name='value')
ldata.head()

date     item     value
0  1959-03-31  realgdp  2710.349
1  1959-03-31     infl     0.000
2  1959-03-31    unemp     5.800
3  1959-06-30  realgdp  2778.801
4  1959-06-30     infl     2.340

date     item     value
0  1959-03-31  realgdp  2710.349
1  1959-03-31     infl     0.000
2  1959-03-31    unemp     5.800
3  1959-06-30  realgdp  2778.801
4  1959-06-30     infl     2.340

**作业2**

ldata通过pivot/unstack恢复data

In [38]:
#请输入ldata使用pivot实现的代码（不得使用unstack）
#pivoted = ldata.pivot(index='date', columns='item', values='value')
#pivoted.head()  #同data.head()

#请输入ldata使用unstack实现的代码（不得使用pivot）
# 将date列转换为索引，并将item列转换为列标签
pivoted = ldata.set_index(['date', 'item'])['value'].unstack()
# 重命名列标签级别的名称
pivoted.columns.name = None

pivoted.head()  #同data.head() 

infl   realgdp  unemp
date                             
1959-03-31  0.00  2710.349    5.8
1959-06-30  2.34  2778.801    5.1
1959-09-30  2.74  2775.488    5.3
1959-12-31  0.27  2785.204    5.6
1960-03-31  2.31  2847.699    5.2

**作业3：**

参照“经营数据分析.xlsx”，求解下列问题，使得输出与结果相同

In [10]:
##  单目标求解
# 年收益=年销售量*(销售单价-单件成本)-设备投资
# 求年收益最佳方案？
df = pd.read_excel("../examples/经营数据分析.xlsx")
# 计算年收益
df['年收益'] = df['年销售量'] * (df['销售单价'] - df['单件成本']) - df['设备投资']
# 按照年收益找最大值，取方案列
best_plan = df.loc[df['年收益'].idxmax(), '方案']
print(df)
print('年收益最高的方案是：', best_plan)


#
# ## 多目标求解 ----
# 期望值=[min(设备投资),min(单件成本),max(年销售量),max(销售单价),
#     max(年收益)];
# 差值=每个方案中，各项数据与期望值的之差的平方和
# 求差值最佳方案？
df = pd.read_excel("../examples/经营数据分析.xlsx")
# 计算年收益
df['年收益'] = df['年销售量'] * (df['销售单价'] - df['单件成本']) - df['设备投资']
# 计算期望值
expected_values = [df['设备投资'].min(), df['单件成本'].min(), df['年销售量'].max(), df['销售单价'].max(), df['年收益'].max()]
# 转换为Series以匹配 df
expected_values = pd.Series(expected_values, index=df.columns[1:])
# 计算差值
df['差值'] = np.sum((df - expected_values) ** 2, axis=1)
# 选择差值最小的方案
best_plan = df.loc[df['差值'].idxmin(), '方案']
# 禁用科学计数法打印
pd.set_option('float_format','{:.0f}'.format)
print(df)
print('差值最小的方案是：', best_plan)


# 不确定性决策分析 ----
## 分析方法
# PLm=pd.DataFrame();# 损益矩阵 ProfitLoss matrix
# PLm['畅销']= 12000*(销售单价-单件成本)-设备投资;
# PLm['一般']= 8000*(销售单价-单件成本)-设备投资;
# PLm['滞销']= 1500*(销售单价-单件成本)-设备投资;
# #
# ## 分析原则----
# # 乐观原则
# lg=损益矩阵三种情况的最大值
#
# # 悲观原则
# bg=损益矩阵三种情况的最小值
#
# # 折中原则
# a=0.65  #65%的乐观概率
# 折中方案= a*lg + (1-a)*bg;
# 求折中最佳方案？
df = pd.read_excel("../examples/经营数据分析.xlsx")
# 计算损益矩阵
PLm = pd.DataFrame()
PLm['畅销'] = 12000 * (df['销售单价'] - df['单件成本']) - df['设备投资']
PLm['一般'] = 8000 * (df['销售单价'] - df['单件成本']) - df['设备投资']
PLm['滞销'] = 1500 * (df['销售单价'] - df['单件成本']) - df['设备投资']
PLm.set_index(df['方案'])
print(PLm)
pd.set_option('float_format', '{:.1f}'.format)
# 计算乐观、悲观和折中方案
mids = []
a = 0.65
for index, row in PLm.iterrows():
    mids.append(row.max() * a + (1-a) * row.min())
PLm['折中'] = mids
PLm.set_index(df['方案'])
print(PLm)
best_plan = df.loc[PLm['折中'].idxmax(), '方案']
print('折中方案最佳方案是：',best_plan)

# #  概率性决策分析 ----
## 期望值法 ----
probE=[0.1,0.65,0.25]; #畅销、一般、滞销的概率
# 期望值=损益矩阵*probE
# 求期望值最佳方案？
df = pd.read_excel("../examples/经营数据分析.xlsx")
# 刷新PLm
PLm = pd.DataFrame()
PLm['畅销'] = 12000 * (df['销售单价'] - df['单件成本']) - df['设备投资']
PLm['一般'] = 8000 * (df['销售单价'] - df['单件成本']) - df['设备投资']
PLm['滞销'] = 1500 * (df['销售单价'] - df['单件成本']) - df['设备投资']

# 利用numpy的dot乘法求出期望值
expected_values = np.dot(PLm, probE)
PLm['期望'] = expected_values
PLm.set_index(df['方案'])

# 设为保留一位小数
print(PLm)
best_plan = df.loc[PLm['期望'].idxmax(), '方案']
print('期望值最佳方案是：',best_plan)


    方案     设备投资  单件成本  年销售量  销售单价      年收益
0  方案1  1500000  1700  8000  2900  8100000
1  方案2  2000000  1550  8000  2900  8800000
2  方案3  2500000  1400  8000  2900  9500000
年收益最高的方案是： 方案3
    方案     设备投资  单件成本  年销售量  销售单价      年收益            差值
0  方案1  1500000  1700  8000  2900  8100000 1960000090000
1  方案2  2000000  1550  8000  2900  8800000  740000022500
2  方案3  2500000  1400  8000  2900  9500000 1000000000000
差值最小的方案是： 方案2


畅销       一般      滞销
方案                            
方案1  12900000  8100000  300000
方案2  14200000  8800000   25000
方案3  15500000  9500000 -250000

         畅销       一般      滞销
0  12900000  8100000  300000
1  14200000  8800000   25000
2  15500000  9500000 -250000


畅销       一般      滞销        折中
方案                                      
方案1  12900000  8100000  300000 8490000.0
方案2  14200000  8800000   25000 9238750.0
方案3  15500000  9500000 -250000 9987500.0

         畅销       一般      滞销        折中
0  12900000  8100000  300000 8490000.0
1  14200000  8800000   25000 9238750.0
2  15500000  9500000 -250000 9987500.0
折中方案最佳方案是： 方案3


畅销       一般      滞销        期望
方案                                      
方案1  12900000  8100000  300000 6630000.0
方案2  14200000  8800000   25000 7146250.0
方案3  15500000  9500000 -250000 7662500.0

         畅销       一般      滞销        期望
0  12900000  8100000  300000 6630000.0
1  14200000  8800000   25000 7146250.0
2  15500000  9500000 -250000 7662500.0
期望值最佳方案是： 方案3
